In [2]:
from tensorflow import keras
import numpy as np
import os
import matplotlib.pyplot as plt
import tensorflow as tf
import cv2 as cv
from sklearn.model_selection import train_test_split
import random
import os
import glob
from PIL import Image, ImageOps
import numpy as np
import shutil
from tensorflow.keras.preprocessing.image import ImageDataGenerator
from tensorflow.keras.applications import EfficientNetB3
from tensorflow.keras.layers import Dense, GlobalAveragePooling2D

In [3]:
base_dir = r"D:\PROJECT\1_MACHINE LEARNING\THESIS_ALL_CLASSIFIER_DATABARU_2\dataset"
subfolders = ["benign", "EarlyPreB", "PreB", "ProB"]
segment_dir = r"D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Segmented"
augment_dir = r"D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented"

In [3]:
# function rotate
def rotate_image(image, angle):
    return image.rotate(angle, expand=True)

In [4]:
def zoom_in_image(image, zoom_factor):
    width, height = image.size
    new_width = int(width / zoom_factor)
    new_height = int(height / zoom_factor)

    left = (width - new_width) / 2
    top = (height - new_height) / 2
    right = (width + new_width) / 2
    bottom = (height + new_height) / 2

    image = image.crop((left, top, right, bottom))
    return image.resize((width, height), Image.Resampling.LANCZOS)

In [5]:
def flip_image(image, direction):
    if direction == 'horizontal':
        return ImageOps.mirror(image)
    elif direction == 'vertical':
        return ImageOps.flip(image)

In [6]:
# bikin subfolder buat augmentation, trus hapus data yg udah ada di dalemnya biar kosong (i think)

for subfolder in subfolders:
  output_folder = os.path.join(augment_dir, subfolder)
  os.makedirs(output_folder, exist_ok=True)
  for filename in os.listdir(output_folder):
    os.remove(os.path.join(output_folder, filename))
  print(f"Isi file dalam folder {output_folder} telah dihapus.")

Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented\benign telah dihapus.
Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented\EarlyPreB telah dihapus.
Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented\PreB telah dihapus.
Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented\ProB telah dihapus.


In [7]:
for subfolder in subfolders:
    subfolder_path = os.path.join(segment_dir, subfolder)
    output_dir = os.path.join(augment_dir, subfolder)
    image_files = glob.glob(os.path.join(subfolder_path, "*"))

    for image_file in image_files:
        original_image = Image.open(image_file)
        rotated_images = [rotate_image(original_image, angle) for angle in [90, 180, 270]]
        flipped_images = [flip_image(original_image, direction) for direction in ['horizontal', 'vertical']]
        zoom_factors = [np.random.uniform(1.2, 2.5) for _ in range(3)]
        zoomed_images = [zoom_in_image(original_image, zoom) for zoom in zoom_factors]

        base_filename = os.path.splitext(os.path.basename(image_file))[0]

        output_paths = [os.path.join(output_dir, f"{base_filename}_rotated_{angle}.jpg") for angle in [90, 180, 270]]
        output_paths += [os.path.join(output_dir, f"{base_filename}_flipped_{direction}.jpg") for direction in ['horizontal', 'vertical']]
        output_paths += [os.path.join(output_dir, f"{base_filename}_zoomed_{i}.jpg") for i in range(1, 4)]

        augmented_images = rotated_images + flipped_images + zoomed_images

        for img, path in zip(augmented_images, output_paths):
            img.save(path)
            print(f"{path} tersimpan")

D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented\benign\Sap_013 (1)_rotated_90.jpg tersimpan
D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented\benign\Sap_013 (1)_rotated_180.jpg tersimpan
D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented\benign\Sap_013 (1)_rotated_270.jpg tersimpan
D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented\benign\Sap_013 (1)_flipped_horizontal.jpg tersimpan
D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented\benign\Sap_013 (1)_flipped_vertical.jpg tersimpan
D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented\benign\Sap_013 (1)_zoomed_1.jpg tersimpan
D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented\benign\Sap_013 (1)_zoomed_2.jpg tersimpan
D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented\benign\Sap_013 (1)_zoomed_3.jpg tersimpan
D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented\benign\Sap_013 (10)_rotated_90.jpg tersimpan
D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented\benign\Sap_01

GABUNGIN DATA ORIGINAL DAN DATA AUGMENTED

In [4]:
import os
import shutil

# Define paths

traindata_dir = r"D:\PROJECT\2_COMPUTER VISION\Image Segmentation\TRAINDATA"

In [14]:
# bikin subfolder buat augmentation, trus hapus data yg udah ada di dalemnya biar kosong (i think)

for subfolder in subfolders:
  output_folder = os.path.join(traindata_dir, subfolder)
  os.makedirs(output_folder, exist_ok=True)
  for filename in os.listdir(output_folder):
    os.remove(os.path.join(output_folder, filename))
  print(f"Isi file dalam folder {output_folder} telah dihapus.")

Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\TRAINDATA\benign telah dihapus.
Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\TRAINDATA\EarlyPreB telah dihapus.
Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\TRAINDATA\PreB telah dihapus.
Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\TRAINDATA\ProB telah dihapus.


In [16]:
# copy data ori ke folder train

for subfolder in subfolders:
  input_folder = os.path.join(segment_dir, subfolder)
  output_folder = os.path.join(traindata_dir, subfolder)
  for img_file in os.listdir(input_folder):
    img_path = os.path.join(input_folder, img_file)
    output_path = os.path.join(output_folder, img_file)
    shutil.copy(img_path, output_path)
    print(f"File {output_path} telah dicopy.")

File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\TRAINDATA\benign\Sap_013 (1).jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\TRAINDATA\benign\Sap_013 (10).jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\TRAINDATA\benign\Sap_013 (11).jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\TRAINDATA\benign\Sap_013 (12).jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\TRAINDATA\benign\Sap_013 (13).jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\TRAINDATA\benign\Sap_013 (14).jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\TRAINDATA\benign\Sap_013 (15).jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\TRAINDATA\benign\Sap_013 (16).jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\TRAINDATA\benign\Sap_013 (17).jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\TRAINDATA\benign\Sap_013 (18).jpg telah

In [ ]:
# copy data augment ke folder train

for subfolder in subfolders:
  input_folder = os.path.join(augment_dir, subfolder)
  output_folder = os.path.join(traindata_dir, subfolder)
  for img_file in os.listdir(input_folder):
    img_path = os.path.join(input_folder, img_file)
    output_path = os.path.join(output_folder, img_file)
    shutil.copy(img_path, output_path)
    print(f"File {output_path} telah dicopy.")

File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\TRAINDATA\benign\Sap_013 (1)_flipped_horizontal.jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\TRAINDATA\benign\Sap_013 (1)_flipped_vertical.jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\TRAINDATA\benign\Sap_013 (1)_rotated_180.jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\TRAINDATA\benign\Sap_013 (1)_rotated_270.jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\TRAINDATA\benign\Sap_013 (1)_rotated_90.jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\TRAINDATA\benign\Sap_013 (1)_zoomed_1.jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\TRAINDATA\benign\Sap_013 (1)_zoomed_2.jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\TRAINDATA\benign\Sap_013 (1)_zoomed_3.jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\TRAINDATA\benign\Sap_013 (10)_flipped_horizontal.

SPLIT TRAIN VAL TEST

In [5]:
split_traindata_dir = r"D:\PROJECT\2_COMPUTER VISION\Image Segmentation\SPLIT_TRAINDATA"

In [6]:
splits = ["train", "test", "val"]
for split in splits:
  for subfolder in subfolders:
    output_folder = os.path.join(split_traindata_dir, split, subfolder)
    os.makedirs(output_folder, exist_ok=True)
    for filename in os.listdir(output_folder):
        os.remove(os.path.join(output_folder, filename))
    print(f"Isi file dalam folder {output_folder} telah dihapus.")

Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\SPLIT_TRAINDATA\train\benign telah dihapus.
Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\SPLIT_TRAINDATA\train\EarlyPreB telah dihapus.
Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\SPLIT_TRAINDATA\train\PreB telah dihapus.
Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\SPLIT_TRAINDATA\train\ProB telah dihapus.
Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\SPLIT_TRAINDATA\test\benign telah dihapus.
Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\SPLIT_TRAINDATA\test\EarlyPreB telah dihapus.
Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\SPLIT_TRAINDATA\test\PreB telah dihapus.
Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\SPLIT_TRAINDATA\test\ProB telah dihapus.
Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\SPLIT_TRAINDATA\val\beni

In [7]:
def split_dataset(base_dir, output_dir, split_ratios=(0.7, 0.2, 0.1)):
    train_dir = os.path.join(output_dir, 'train')
    val_dir = os.path.join(output_dir, 'val')
    test_dir = os.path.join(output_dir, 'test')

    for subfolder in subfolders:
        subfolder_dir = os.path.join(base_dir, subfolder)
        images = [os.path.join(subfolder_dir, img) for img in os.listdir(subfolder_dir) if img.lower().endswith(('.png', '.jpg', '.jpeg', '.bmp', '.gif'))]

        random.shuffle(images)

        total_images = len(images)
        train_count = int(total_images * split_ratios[0])
        val_count = int(total_images * split_ratios[1])

        train_images = images[:train_count]
        val_images = images[train_count:train_count + val_count]
        test_images = images[train_count + val_count:]

        for image in train_images:
            shutil.copy(image, os.path.join(train_dir, subfolder, os.path.basename(image)))
        for image in val_images:
            shutil.copy(image, os.path.join(val_dir, subfolder, os.path.basename(image)))
        for image in test_images:
            shutil.copy(image, os.path.join(test_dir, subfolder, os.path.basename(image)))

        print(f'Kategori {subfolder}: {train_count} gambar untuk train, {val_count} gambar untuk val, {total_images - train_count - val_count} gambar untuk test.')

split_dataset(traindata_dir, split_traindata_dir)

Kategori benign: 3225 gambar untuk train, 921 gambar untuk val, 462 gambar untuk test.
Kategori EarlyPreB: 6167 gambar untuk train, 1762 gambar untuk val, 882 gambar untuk test.
Kategori PreB: 6016 gambar untuk train, 1719 gambar untuk val, 860 gambar untuk test.
Kategori ProB: 5014 gambar untuk train, 1432 gambar untuk val, 718 gambar untuk test.
